In [ ]:
%load_ext autoreload
%autoreload 2

In [1]:
import pyvista as pv
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
from pathlib import Path

In [2]:
p  = !pwd
root=Path(p[0])

In [3]:
ROOT = root.parent
marv_obj = ROOT / "meshes/marv_lid.obj"
test_mesh = pv.read(marv_obj)

FileNotFoundError: File (/Users/davidkorcak/Documents/ctu/bachelors/flipper_training/meshes/marv_lid.obj) not found

In [ ]:
test_mesh.plot()

2025-02-21 12:42:27.276 Python[7218:2510997] ApplePersistenceIgnoreState: Existing state will not be touched. New state will be written to /var/folders/yj/_6b0pqvs5xg33v_xy5q2v9_40000gn/T/org.python.python.savedState


Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x1073f91c0_0&reconnect=auto" class="pyvista…

In [ ]:
import yaml
with open(root.parent / f"robots/marv.yaml", "r") as file:
    robot_params = yaml.safe_load(file)

In [ ]:
import torch
driving_part_bboxes = [torch.tensor(p["bbox"]) for p in robot_params["driving_parts"]]
body_bbox = torch.tensor(robot_params["body"]["bbox"])

In [ ]:
robot_points = torch.tensor(pv.read(str(marv_obj)).points)

In [ ]:
assert test_mesh.is_all_triangles

In [ ]:
import pyacvd


def extract_flipper_points_from_mesh(mesh: pv.PolyData, n_points: int = 100, **clus_opts) -> torch.Tensor:
    delaunay = mesh.delaunay_3d()
    surf = delaunay.extract_surface()
    clus: pyacvd.Clustering = pyacvd.Clustering(surf)
    clus.cluster(n_points, **clus_opts)
    return torch.tensor(clus.cluster_centroid)

In [ ]:
from flipper_training.utils.geometry import points_in_oriented_box, points_within_bbox

In [ ]:
driving_meshes = []
driving_points = []
faces = test_mesh.faces.reshape(-1, 4)[:, 1:]
for p in driving_part_bboxes:
    mask = points_within_bbox(robot_points, p)
    nonzero = mask.nonzero().numpy().flatten()
    pointgrid = test_mesh.extract_points(nonzero, adjacent_cells=False, include_cells=True)
    driving_meshes.append(pointgrid)
    driving_points.append(extract_flipper_points_from_mesh(pointgrid, 200))

2025-02-21 13:23:36.199 (2470.089s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:23:36.342 (2470.232s) [          265095]      vtkDelaunay3D.cxx:514   WARN| vtkDelaunay3D (0x3ae72f920): 66 degenerate triangles encountered, mesh quality suspect
2025-02-21 13:23:36.590 (2470.480s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:23:36.736 (2470.626s) [          265095]      vtkDelaunay3D.cxx:514   WARN| vtkDelaunay3D (0x3b1138db0): 48 degenerate triangles encountered, mesh quality suspect
2025-02-21 13:23:36.989 (2470.879s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:23:37.130 (2471.020s) [          265095]      vtkDelaunay3D.cxx:514   WARN| vtkDelaunay3D (0x3b1130690): 59 degenerate triangles encountered, mesh quality suspect
2025-02-21 13:23:37.378 (2471.268s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor

In [ ]:
driving_meshes[0].plot(render_points_as_spheres=True)

Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x3508a9550_22&reconnect=auto" class="pyvist…

In [ ]:
delaunay = driving_meshes[0].delaunay_3d()
delaunay.plot()

2025-02-21 13:23:42.365 (2476.256s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:23:42.509 (2476.399s) [          265095]      vtkDelaunay3D.cxx:514   WARN| vtkDelaunay3D (0x3b11f1ea0): 66 degenerate triangles encountered, mesh quality suspect


Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x32958b320_23&reconnect=auto" class="pyvist…

In [ ]:
surface = delaunay.extract_surface()
surface_points = pv.PolyData(surface.points)
surface_points.plot(render_points_as_spheres=True, point_size=10,)

Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x3508aa810_24&reconnect=auto" class="pyvist…

In [ ]:
import pyacvd

In [ ]:
clus = pyacvd.Clustering(surface)
clus.cluster(192, maxiter=1000, iso_try=50)

array([  0,   1,   0, ..., 100,  42,  42], shape=(1899,), dtype=int32)

In [ ]:
pv.PolyData(clus.cluster_centroid).plot(render_points_as_spheres=True, point_size=10,)

Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x3508a8bf0_25&reconnect=auto" class="pyvist…

In [ ]:
body_mask = points_within_bbox(robot_points, body_bbox)
nonzero = body_mask.nonzero().numpy().flatten()
body_mesh = test_mesh.extract_points(nonzero, adjacent_cells=False, include_cells=True).extract_surface().triangulate()

In [ ]:
body_mesh.plot()

Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x17c16d460_1&reconnect=auto" class="pyvista…

In [ ]:
filled_body = body_mesh.delaunay_3d().extract_surface()

2025-02-21 13:11:31.674 (1745.561s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:11:31.674 (1745.561s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:11:31.674 (1745.561s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:11:31.674 (1745.561s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:11:31.674 (1745.561s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:11:31.674 (1745.561s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:11:31.675 (1745.561s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:11:31.675 (1745.561s) [          265095]            vtkMath.cxx:570   WARN| Unable to factor linear system
2025-02-21 13:11:31.675 (1745.56

In [ ]:
import trimesh

In [ ]:
vertices = body_mesh.points
faces = body_mesh.faces.reshape(-1, 4)[:, 1:]

In [ ]:
body_trimesh = trimesh.Trimesh(vertices=vertices, faces=faces)

In [ ]:
body_trimesh.show()

In [ ]:
chull = body_trimesh.convex_hull
pts = trimesh.sample.sample_surface_even(chull, 193)[0]
pv.PolyData(pts).plot(render_points_as_spheres=True, point_size=10,)

Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x329623140_36&reconnect=auto" class="pyvist…

In [ ]:
vox = trimesh.voxel.creation.voxelize(body_trimesh, pitch=0.01)

In [ ]:
vox.show()

In [ ]:
from trimesh.voxel import morphology

# Apply binary closing to seal small cavities
filled_encoding = morphology.binary_closing(vox.encoding, structure=np.ones((3, 3, 3)))
filled_vox = trimesh.voxel.VoxelGrid(filled_encoding, transform=vox.transform)

In [ ]:
pv_points = pv.PolyData(filled_vox.points)
pv_points.plot(render_points_as_spheres=True, point_size=10,)

Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x321ce76e0_6&reconnect=auto" class="pyvista…

In [ ]:
driving_meshes[0].plot(render_points_as_spheres=True,style="points")

Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x35086c200_26&reconnect=auto" class="pyvist…

In [ ]:
flipper = driving_meshes[0].extract_surface()
flipper_verts = flipper.points
flipper_faces = flipper.faces.reshape(-1, 4)[:, 1:]
flipper_trimesh = trimesh.Trimesh(vertices=flipper_verts, faces=flipper_faces)
flipper_trimesh.show()

In [ ]:
flipper_chull = flipper_trimesh.convex_hull
flipper_pts = trimesh.sample.sample_surface_even(flipper_chull, 193)[0]
pv.PolyData(flipper_pts).plot(render_points_as_spheres=True, point_size=10,)


Widget(value='<iframe src="http://localhost:56173/index.html?ui=P_0x3282da870_35&reconnect=auto" class="pyvist…